In [0]:
import pandas as pd
import re
import numpy as np
from collections import *
from random import sample, random
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import mean_squared_error
from datetime import datetime
from zipfile import ZipFile, ZIP_DEFLATED
import os
from sklearn.model_selection import GridSearchCV
from random import choice
import xgboost
import joblib
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVR

In [0]:
from google.colab import files
uploaded = files.upload()


In [0]:
pd.options.display.max_colwidth = 100

# train_in = pd.read_csv('./task2_data/train.csv', index_col='buyer')
# meta_in = pd.read_csv('./task2_data/meta.csv', index_col='id_tov')
train_in = pd.read_csv('./train.csv', index_col='buyer')
meta_in = pd.read_csv('./meta.csv', index_col='id_tov')

meta = pd.DataFrame.copy(meta_in)

In [0]:
pd.read_csv('./meta.csv')

id_tov                                            Наименование      Вес  \
0         23                                          Молоко ЦЕЛЬНОЕ     1 л    
1         81                                             Молоко 3,2%      1 л   
2        109                                  Молоко топлёное, 500 г   500 г    
3       1785                                             Молоко 2,5%   450 г    
4        377                                   Молоко 3,2% в бутылке  900 мл    
5        437                                Молоко цельное в бутылке  900 мл    
6        596                                               Молоко 1%  450 мл    
7        720                                     Молоко безлактозное    500 г   
8        395                                Масса творожная с изюмом   300 г    
9        307                             Творог с шоколадной крошкой   125 г    
10       512                                            Творог Вишня   125 г    
11       818                         Творог мягкий "Инжир-чернослив"    125 г   
12       826                                  Творог мягкий "Клюква"   125 г    
13       829                          Творог "Зёрнышко" обезжиренный    280 г   
14       927                    Творог зернёный с киви и крыжовником    150 г   
15      1011                   Творог "Пластовой" из цельного молока    350 г   
16      1695                                 Сырок творожный с какао     40 г   
17      1696                    Сырок творожный с кокосовой стружкой     40 г   
18      1832                                     Творог Домашний 18%   200 г    
19      1849                                     Творог обезжиренный   200 г    
20      2038                                          Творог Черника   125 г    
21        33                                  Творог зернёный, 230 г   230 г    
22        87                                               Творог 5%   400 г    
23        90                                               Творог 9%   400 г    
24       467                     Сырок творожный в молочном шоколаде     40 г   
25       472                              Творог мягкий злаки-ваниль   125 г    
26       502                           Творог мягкий обезжиренный 0%   120 г    
27       503                                      Творог мягкий 4,5%    120 г   
28       526                    Сырок творожный со сгущённым молоком    40 г    
29      1097  Творог мягкий "Черная смородина" без добавления сахара    125 г   
...      ...                                                     ...      ...   
2041    1454                                      х/б изд. "Луковые"    150 г   
2042    1597                                    Булочка Михайловская     35 г   
2043    1453                                   х/б изд."Версальские"    350 г   
2044    1444                        Изд.булочное " Пулиш с отрубями"    350 г   
2045    1446                    Изделия хлебобулочные  "Деревенские"    300 г   
2046    1919                       Изделие хлебобулочное «Гречишное»    100 г   
2047    1920                         Изделие «Домашнее бездрожжевое»    400 г   
2048    1921                         Изделие «Заварное бездрожжевое»    330 г   
2049    1923                         Изделие хлебобулочное «Степное»    300 г   
2050      86                                             Вак - беляш    100 г   
2051      88                                             Зур - беляш    190 г   
2052      94                                     Капустник с курицей    120 г   
2053      89                                                  Курник    120 г   
2054      93                                                   Самса    100 г   
2055      91                                                Учпучмак    110 г   
2056    1452                               Слойка с сыром и ветчиной     80 г   
2057    1450                            Слойка с творогом и шпинатом     80 г   
2058    1457                         

In [0]:
# scaler =  StandardScaler()
# scaled = meta.copy()
# scaled = scaled.drop(columns=[scaled.columns[0]])
# to_scale = ['belki', 'jiri', 'uglevodi', 'kkal', 'time']
# features = scaled[to_scale]
# scaler = StandardScaler().fit(features.values)
# features = scaler.transform(features.values)
# scaled[to_scale] = features
# scaled

In [0]:
train_in


items
buyer                                                                                   
4            101 1933 1828 1135 1367 1906 1629 1533 1874 1775 836 1360 259 429 1640 1914
11              1795 844 1214 1527 447 77 1925 719 1385 1475 194 1391 534 2017 1719 2067
34                        1596 389 31 269 658 801 109 185 220 296 962 351 2036 1458 1671
37             1234 453 1214 680 1706 1708 1506 1151 1949 1178 987 1665 1992 1819 87 120
44                       249 1234 986 824 437 975 676 1447 413 282 1743 1149 657 889 261
95                    1646 975 978 1970 1149 1946 1705 1706 688 1633 691 80 1087 532 800
119                   1302 968 28 136 418 1546 518 65 1111 14 274 1470 1083 698 580 1882
121                         1234 474 931 31 374 1235 247 819 248 842 360 505 377 754 843
134                      693 1596 136 139 1723 1975 71 2002 376 220 81 505 351 1513 1182
159                  762 1373 1948 290 291 540 1173 627 1574 1740 1288 1715 118 1346 508
166                1247 1073 682 311 683 1547 933 934 333 334 932 1354 1903 1235 842 869
198                            1629 646 817 265 1936 845 1204 733 1947 948 1218 645 1752
205                       437 668 1099 107 503 294 443 444 1124 505 673 674 1613 87 1458
211                    874 220 960 222 251 1959 1779 1270 914 750 378 1126 1974 768 1915
219                             292 898 136 139 351 931 1877 532 841 1990 90 819 308 772
240      327 437 1521 316 58 1230 1273 362 1036 1535 1663 1342 1475 377 592 23 1915 1671
253                         202 1646 2051 2052 2053 827 363 1959 898 1795 1468 1904 2038
271                                 249 605 1336 1959 1656 929 137 377 818 1481 1554 308
304                                274 1396 1303 1646 639 1795 313 1481 356 1306 592 784
322                                  274 1131 403 1266 1894 377 1116 948 335 90 1458 563
336             813 453 403 211 1225 478 894 1558 1178 1258 1611 1390 1612 1719 1289 756
363                 1023 1959 438 497 740 138 1723 625 292 160 836 81 1689 674 1346 1458
364                          185 1132 363 1475 351 2017 1568 1973 1230 1354 109 1458 664
374                               501 1644 1256 1220 129 252 1378 733 1882 1458 1751 509
383                         1756 297 437 1958 1796 1006 471 505 411 1338 118 247 248 151
387                              314 212 1115 81 58 1733 137 933 23 1877 269 1913 50 326
392                          970 971 1646 1958 1959 477 291 445 1726 563 412 377 87 1458
394                         408 363 364 720 81 803 1626 1103 497 865 1135 87 1126 335 23
454          1755 329 1931 512 1764 765 659 71 501 249 503 1151 360 526 527 838 87 23 92
495                1024 1690 27 1756 1793 596 490 1653 844 501 788 1197 481 1927 87 1119
...                                                                                  ...
1441992             383 356 1721 497 635 1603 731 392 525 1559 1233 486 90 2070 1458 371
1442001                     1542 1208 1304 165 1934 670 1390 1108 806 1270 1233 379 1080
1442060      925 1620 1132 1703 1702 1677 29 1846 1990 1355 71 1219 81 989 1117 2068 664
1442097                                   1606 503 298 140 101 943 1579 1269 1481 33 645
1442105      1265 1347 403 1563 387 65 1253 1948 1707 350 249 900 577 194 1640 1587 1671
1442136                                1532 525 162 58 962 319 1550 1551 377 269 790 326
1442144            1695 1533 294 2027 1658 394 1266 1038 300 930 2019 1149 733 1973 1975
1442239   1334 2026 262 129 437 417 422 1898 464 244 1469 582 109 1830 253 1387 946 1671
1442295                              249 925 1312 526 1959 1266 641 265 351 807 291 1915
1442297          1563 1564 1961 345 1723 290 625 2003 681 221 363 1407 160 1779 1720 949
1442307      1646 437 668 338 497 357 935 64 293 81 803 2012 671 90 22 48 87 790 23 1458
1442383               438 914 1149 1975 2000 1382 802 1788 81 505 1090 947 87 90 23 1458
1442422          1081 2027 1889 771 1535 1536 1537 928 1854 1894 1288 1469 194

### Считаем количество вхождений товаров в чью-либо историю покупок

In [0]:
def get_goods_occurances(train):
    goods_occurances = {}
    for card_id in tqdm(train.index):
        goods_ids = list(train.loc[[card_id]]['items'])[0].split(' ')
        for product_id in goods_ids:
            if product_id in goods_occurances.keys():
                goods_occurances[product_id] += 1
            else:
                goods_occurances[product_id] = 1
    return goods_occurances

In [0]:
goods_occurances = get_goods_occurances(train_in)

100%|██████████| 65950/65950 [00:57<00:00, 1146.67it/s]


### Отбрасываем те товары которые никто не покупал

Товаров было: 2071

Товаров стало: 1888

In [0]:
meta_in.shape

(2071, 7)

In [0]:
for index, row in meta_in.iterrows():
    if str(index) not in goods_occurances.keys():
        meta_in.drop(index, inplace=True)

In [0]:
meta_in

Наименование      Вес  \
id_tov                                                                    
23                                              Молоко ЦЕЛЬНОЕ     1 л    
81                                                 Молоко 3,2%      1 л   
109                                     Молоко топлёное, 500 г   500 г    
1785                                               Молоко 2,5%   450 г    
377                                      Молоко 3,2% в бутылке  900 мл    
437                                   Молоко цельное в бутылке  900 мл    
596                                                  Молоко 1%  450 мл    
720                                        Молоко безлактозное    500 г   
395                                   Масса творожная с изюмом   300 г    
307                                Творог с шоколадной крошкой   125 г    
512                                               Творог Вишня   125 г    
818                            Творог мягкий "Инжир-чернослив"    125 г   
826                                     Творог мягкий "Клюква"   125 г    
829                             Творог "Зёрнышко" обезжиренный    280 г   
927                       Творог зернёный с киви и крыжовником    150 г   
1011                     Творог "Пластовой" из цельного молока    350 г   
1695                                   Сырок творожный с какао     40 г   
1696                      Сырок творожный с кокосовой стружкой     40 г   
1832                                       Творог Домашний 18%   200 г    
1849                                       Творог обезжиренный   200 г    
2038                                            Творог Черника   125 г    
33                                      Творог зернёный, 230 г   230 г    
87                                                   Творог 5%   400 г    
90                                                   Творог 9%   400 г    
467                        Сырок творожный в молочном шоколаде     40 г   
472                                 Творог мягкий злаки-ваниль   125 г    
502                              Творог мягкий обезжиренный 0%   120 г    
503                                         Творог мягкий 4,5%    120 г   
526                       Сырок творожный со сгущённым молоком    40 г    
1097    Творог мягкий "Черная смородина" без добавления сахара    125 г   
...                                                        ...      ...   
1861                                          Леденец Ягодныи?    35 г    
2028                                    Напиток "Хлорелла", ВП   250 мл   
1372                              Печенье с кусочками шоколада     45 г   
1440                                                  Круассан     65 г   
1455                      Булочка - рулетик творожная с вишней    100 г   
1456                                       Плюшка «Московская»     75 г   
1449                                 Слойка "Венская" с изюмом     60 г   
1448                                Слойка "Венская" с корицей     60 г   
1451                               Слойка с фруктовой начинкой     80 г   
1323                                           Тарт "Лимонный"    200 г   
1454                                        х/б изд. "Луковые"    150 г   
1597                                      Булочка Михайловская     35 г   
1453                                     х/б изд."Версальские"    350 г   
1444                          Изд.булочное " Пулиш с отрубями"    350 г   
1446                      Изделия хлебобулочные  "Деревенские"    300 г   
1919                         Изделие хлебобулочное «Гречишное»    100 г   
1920                           Изделие «Домашнее бездрожжевое»    400 г   
1921                           Изделие «Заварное бездрожжевое»    330 г   
1923                           Изделие хлебобулочное «Степное»    300 г   
1452                                 Слойка с сыром и ветчиной     80 г   
1450                              Слойка с творогом и шпинатом     80 г   


### Получаем фичи: белки, жиры, углеводы, ккал

Товаров было: 1888

Товаров стало: 1435

In [0]:
re.sub("[^0-9.]", "", "aas30ds.a20")

'30.20'

In [0]:
meta = pd.DataFrame(index=meta_in.index)

meta['belki'] = float('NaN')
meta['jiri'] = float('NaN')
meta['uglevodi'] = float('NaN')
meta['kkal'] = float('NaN')

for index, row in tqdm(meta_in.iterrows()):
    
    nutrients_raw = str(row['Пищевая ценность']).split()
    
    if 'nan' in nutrients_raw:
        meta.drop(index, inplace=True)
        continue
        
    if 'белки' in nutrients_raw:
        b_idx = nutrients_raw.index('белки')
        try:
            b_value = float(re.sub("[^0-9.]", "", nutrients_raw[b_idx+1].replace(',','.')))
            meta.at[index, 'belki'] = b_value
        except Exception as e:
            meta.at[index, 'belki'] = float("NaN")
            
    if 'жиры' in nutrients_raw:
        j_idx = nutrients_raw.index('жиры')
        try:
            j_value = float(re.sub("[^0-9.]", "", nutrients_raw[j_idx+1].replace(',','.')))
            meta.at[index, 'jiri'] = j_value
        except Exception as e:
            meta.at[index, 'jiri'] = float("NaN")
            
    if 'углеводы' in nutrients_raw:
        u_idx = nutrients_raw.index('углеводы')
        try:
            u_value = float(re.sub("[^0-9.]", "", nutrients_raw[u_idx+1].replace(',', '.')))
            meta.at[index, 'uglevodi'] = u_value
        except Exception as e:
            meta.at[index, 'uglevodi'] = float("NaN")
            
    if 'ккал' in nutrients_raw:
        k_idx = nutrients_raw.index('ккал')
        try:
            k_value = float(nutrients_raw[k_idx-1].replace(',', '.'))
            meta.at[index, 'kkal'] = k_value
        except Exception as e:
            meta.at[index, 'kkal'] = float("NaN")

print(meta.shape)

1888it [00:00, 2781.20it/s]

(1435, 4)


In [0]:
meta.head(15)

belki  jiri  uglevodi   kkal
id_tov                              
23        NaN   NaN       5.0   70.0
81        3.0   3.2       4.7   60.0
109       3.0   4.0       4.7   67.0
1785      3.0   2.5       4.7   53.0
377       3.0   3.2       4.7   60.0
437       2.8   NaN       4.7    NaN
596       3.0   1.0       4.7   40.0
720       3.0   NaN       NaN   75.0
395      12.8  16.5      10.5  242.0
307       7.0   6.7      10.0  128.3
512       7.0   6.0       9.0  118.0
818       7.3   6.0      10.5  125.0
826       7.0   6.0      10.0  122.0
829      18.0   NaN       3.3  101.0
927      10.8   5.0       2.8   99.4

### Сбрасываем все товары у которых NaN в одной из позиций (белки \ жиры \ углеводы \ ккал)

Товаров было: 1435

Товаров стало: 992

In [0]:
meta.dropna(inplace=True)

meta.shape

(992, 4)

### Получаем фичу: time

Было товаров: 992

Стало товаров: 989

In [0]:
only_words = re.compile(r'[а-яА-Я]{1,}')
only_numbers = re.compile(r'[1-9]{1,}')

def parse_time(string):
    if not isinstance(string, str):
        return 0
    elif 'ограничен' in string:
        return -1
    else:
        time = int(only_numbers.findall(string)[0])

        if 'лет' in string or 'год' in string:
            return float(time * 365)

        elif 'месяц' in string:
            return float(time * 30)

        elif 'сут' in string or 'день' in string or 'дней' in string or 'дня' in string:
            return float(time)

        elif 'час' in string:
            return float(time / 24)
        else:
            raise ValueError('Забыли про %s' % string)


for index, row in tqdm(meta.iterrows()):
    time = parse_time(meta_in.at[index, 'Срок годности'])
    if time == 0:
        meta.drop(index, inplace=True)
    else:
        meta.at[index, 'time'] = time
    

992it [00:00, 10952.97it/s]


In [0]:
meta.shape

(989, 5)

In [0]:
meta.head(10)

belki  jiri  uglevodi   kkal  time
id_tov                                    
81        3.0   3.2       4.7   60.0   5.0
109       3.0   4.0       4.7   67.0   6.0
1785      3.0   2.5       4.7   53.0   5.0
377       3.0   3.2       4.7   60.0   5.0
596       3.0   1.0       4.7   40.0   5.0
395      12.8  16.5      10.5  242.0   4.0
307       7.0   6.7      10.0  128.3   6.0
512       7.0   6.0       9.0  118.0   6.0
818       7.3   6.0      10.5  125.0   6.0
826       7.0   6.0      10.0  122.0   6.0

### Фильтруем train оставляя лишь отфильтрованные товары

In [0]:
train

items
buyer                                                                   
4                                           1933 1533 1775 836 1360 1640
11                                                  1214 77 719 534 1719
34                         1596 389 31 269 109 185 296 962 351 2036 1458
37                     1234 453 1214 1506 1151 1949 1178 987 1819 87 120
44                                                 1234 824 676 1447 261
95                                                      688 691 1087 532
119            1302 968 28 136 1546 518 65 14 274 1470 1083 698 580 1882
121                                  1234 31 374 819 842 360 377 754 843
134                            1596 136 139 1723 1975 71 376 81 351 1182
159                        762 1373 1948 540 627 1740 1288 1715 118 1346
166                 1247 1073 682 311 683 1547 933 934 932 1354 1903 842
198                                               646 817 1936 1218 1752
205                            668 1099 503 443 444 673 674 1613 87 1458
211                              960 1959 1270 914 750 378 1126 1974 768
219                               292 136 139 351 532 841 90 819 308 772
240                                   1521 316 58 1230 362 1036 1342 377
253                           2051 2052 2053 827 363 1959 1468 1904 2038
271                                            1959 137 377 818 1554 308
304                                                274 1396 1303 313 356
322                           274 1131 403 1894 377 1116 335 90 1458 563
336       813 453 403 211 478 894 1558 1178 1258 1611 1390 1612 1719 756
363      1959 438 497 740 138 1723 625 292 160 836 81 1689 674 1346 1458
364                                  185 363 351 1568 1230 1354 109 1458
374                                                   501 1882 1458 1751
383                                                1756 297 471 1338 118
387                                   212 1115 81 58 137 933 269 1913 50
392                                 970 971 1959 477 445 563 377 87 1458
394                              408 363 81 803 1103 497 865 87 1126 335
454          1755 329 1931 512 659 71 501 503 1151 360 526 527 838 87 92
495                      27 1756 1793 596 490 1653 501 1197 1927 87 1119
...                                                                  ...
1441992           383 356 1721 497 635 731 392 525 1559 1233 90 1458 371
1442001              1542 1304 165 1934 670 1390 1108 1270 1233 379 1080
1442060                                      925 29 1846 1355 71 1219 81
1442097                                    1606 503 298 943 1579 1269 33
1442105                         1265 403 1563 65 1253 1948 577 1640 1587
1442136                         525 162 58 962 319 1550 1551 377 269 790
1442144                                      1695 1533 394 1038 930 1975
1442239                          1334 2026 417 422 1898 244 109 1387 946
1442295                                                 925 526 1959 351
1442297            1563 1564 1961 345 1723 625 681 363 1407 160 1720 949
1442307               668 338 497 935 64 81 803 671 90 22 48 87 790 1458
1442383                         438 914 1975 2000 1382 802 81 87 90 1458
1442422                                               1889 1894 1288 982
1442455             1207 1073 596 1564 2036 1715 963 377 827 87 1091 371
1442526                                   1917 1197 1878 64 335 336 1975
1442529                   775 356 58 64 335 87 2008 1037 81 484 1587 371
1442551                 810 545 646 512 836 81 316 1387 1097 862 864 750
1442570                                                    313 1269 1275
1442576                       736 239 549 11 1101 574 1120 719 1342 1288
1442590                   1265 212 385 1270 726 2001 15 81 671 1329 1458
1442603                                         1230 699 1580 686 818 65
1442633                         182 1785 1625 456 35 1082 1662 1586 1126
1442643                               773 774 686 27

In [0]:
train = pd.DataFrame(index=train_in.index)

# SELECT 'belki' FROM META WHERE belki > 5.0;
# META[['col1', 'col2, belki']][META[belki] > 5.0] 
for index, row in train_in.iterrows(): # итерируемся по строчкам
    bought = [int(x) for x in row[0].split()]
    filtered_bought = []
    for product in bought:
        if product in meta.index:
            filtered_bought.append(product)    
    train.at[index, 'items'] = ' '.join([str(x) for x in filtered_bought])

In [0]:
from itertools import groupby
for index, row in train_in.iterrows(): # итерируемся по строчкам
    bought = set([int(x) for x in row[0].split()])
    freqs=[len(list(group)) for key, group in groupby(bought)]
    for freq in freqs:
      if freq > 1:
        print("DOUBLE")
        break

In [0]:
train.head(10)

items
buyer                                                           
4                                   1933 1533 1775 836 1360 1640
11                                          1214 77 719 534 1719
34                 1596 389 31 269 109 185 296 962 351 2036 1458
37             1234 453 1214 1506 1151 1949 1178 987 1819 87 120
44                                         1234 824 676 1447 261
95                                              688 691 1087 532
119    1302 968 28 136 1546 518 65 14 274 1470 1083 698 580 1882
121                          1234 31 374 819 842 360 377 754 843
134                    1596 136 139 1723 1975 71 376 81 351 1182
159                762 1373 1948 540 627 1740 1288 1715 118 1346

### Sanity check

In [0]:
meta['cat'] = meta_in['Категория'].astype('category').cat.codes
meta['subcat'] = meta_in['Подкатегория'].astype('category').cat.codes

In [0]:
meta

belki     jiri  uglevodi    kkal   time  cat  subcat
id_tov                                                       
81       3.000   3.2000    4.7000   60.00    5.0    9      48
109      3.000   4.0000    4.7000   67.00    6.0    9      48
1785     3.000   2.5000    4.7000   53.00    5.0    9      48
377      3.000   3.2000    4.7000   60.00    5.0    9      48
596      3.000   1.0000    4.7000   40.00    5.0    9      48
395     12.800  16.5000   10.5000  242.00    4.0    9     103
307      7.000   6.7000   10.0000  128.30    6.0    9     103
512      7.000   6.0000    9.0000  118.00    6.0    9     103
818      7.300   6.0000   10.5000  125.00    6.0    9     103
826      7.000   6.0000   10.0000  122.00    6.0    9     103
927     10.800   5.0000    2.8000   99.40    1.0    9     103
1695    15.000  11.0000   34.0000  295.00    7.0    9     103
1696    15.000  11.0000   32.0000  305.00    7.0    9     103
1832    14.000  18.0000    2.8000  232.00    5.0    9     103
1849    18.000   1.0000    2.0000   88.50    5.0    9     103
2038     7.000   6.0000   12.5000  132.00    6.0    9     103
33      15.000   4.0000    1.5000  102.00    5.0    9     103
87      16.000   5.0000    3.0000  121.00    3.0    9     103
90      16.000   9.0000    3.0000  157.00    3.0    9     103
467     15.000  11.0000   32.0000  287.00    8.0    9     103
472      7.000   6.0000   12.0000  128.00    6.0    9     103
503      8.000   4.5000    2.5000   83.00    6.0    9     103
526     14.000  11.0000   33.0000  287.00    7.0    9     103
1097     7.300   6.0000   10.0000  123.20    6.0    9     103
1151    16.000   5.0000    3.0000  121.00    8.0    9     103
1231     6.900   6.0000    4.0000  101.00    5.0    9     103
1285     7.000   3.9000    3.0000   75.00    1.0    9     103
1333    10.600   9.0000    3.3000  137.00   12.0    9     103
1483    16.000   9.0000    3.4000  158.60    8.0    9     103
1580    10.800   5.0000    2.8000   99.40    1.0    9     103
...        ...      ...       ...     ...    ...  ...     ...
996      0.500   0.1000   80.1000  323.00  180.0   18      44
1861     0.040   0.0300   90.3000  339.40  180.0   18      44
2028     0.056   0.0067    0.0112    0.34  180.0    3      31
1372     6.300  26.7000   61.5000  511.00    7.0   15      84
1440     6.200  27.0000   32.0000  400.00    1.0   15      84
1455     8.000  10.8000   48.8000  324.00    1.0   15      84
1456     8.000   7.7000   58.5000  355.00    1.0   15      84
1449     5.100  21.0000   39.0000  370.00    1.0   15      84
1448     5.700  26.0000   33.0000  390.00    1.0   15      84
1451     3.800  15.0000   46.0000  330.00    1.0   15      84
1323     3.500  13.0000   59.0000  370.00    2.0   15      84
1454     7.500   2.0000   50.0000  250.00    1.0   15      47
1597     6.000   1.0000   46.0000  220.00    1.0   15      47
1453     8.000   4.0000   56.0000  290.00    1.0   15     110
1444     8.000   0.8000   47.0000  230.00    1.0   15     110
1446     7.000   1.0000   50.0000  240.00    1.0   15     110
1919    10.700   3.4000   56.3000  298.60    1.0   15     110
1920     7.100   0.6000   59.3000  271.00    1.0   15     110
1921     7.800   0.6000   56.2000  261.40    1.0   15     110
1923     8.300   2.3000   56.1000  278.30    1.0   15     110
1452     8.800  20.0000   36.0000  360.00    1.0   15     101
1450    11.000  23.0000   38.0000  400.00    1.0   15     101
1457     3.200   7.8000   30.8000  206.20    1.0   15     101
1463    14.200  11.7000   29.3000  279.30    1.0   15     101
1462     5.200  15.9000   28.0000  275.90    1.0   15     101
1460    12.000  10.5000   30.3000  263.70    1.0   15     101
1441     8.000   0.7000   55.0000  260.00    1.0   15      13
1442     8.000   6.0000   44.0000  265.00    1.0   15      13
1439     7.000   0.7000   48.0000  230.00    1.0   15      13
1598    14.500   3.2000    7.4000  116.40   36.0   16      62

[989 rows x 7 columns]

In [0]:
meta

belki     jiri  uglevodi    kkal   time  cat  subcat
id_tov                                                       
81       3.000   3.2000    4.7000   60.00    5.0    9      48
109      3.000   4.0000    4.7000   67.00    6.0    9      48
1785     3.000   2.5000    4.7000   53.00    5.0    9      48
377      3.000   3.2000    4.7000   60.00    5.0    9      48
596      3.000   1.0000    4.7000   40.00    5.0    9      48
395     12.800  16.5000   10.5000  242.00    4.0    9     103
307      7.000   6.7000   10.0000  128.30    6.0    9     103
512      7.000   6.0000    9.0000  118.00    6.0    9     103
818      7.300   6.0000   10.5000  125.00    6.0    9     103
826      7.000   6.0000   10.0000  122.00    6.0    9     103
927     10.800   5.0000    2.8000   99.40    1.0    9     103
1695    15.000  11.0000   34.0000  295.00    7.0    9     103
1696    15.000  11.0000   32.0000  305.00    7.0    9     103
1832    14.000  18.0000    2.8000  232.00    5.0    9     103
1849    18.000   1.0000    2.0000   88.50    5.0    9     103
2038     7.000   6.0000   12.5000  132.00    6.0    9     103
33      15.000   4.0000    1.5000  102.00    5.0    9     103
87      16.000   5.0000    3.0000  121.00    3.0    9     103
90      16.000   9.0000    3.0000  157.00    3.0    9     103
467     15.000  11.0000   32.0000  287.00    8.0    9     103
472      7.000   6.0000   12.0000  128.00    6.0    9     103
503      8.000   4.5000    2.5000   83.00    6.0    9     103
526     14.000  11.0000   33.0000  287.00    7.0    9     103
1097     7.300   6.0000   10.0000  123.20    6.0    9     103
1151    16.000   5.0000    3.0000  121.00    8.0    9     103
1231     6.900   6.0000    4.0000  101.00    5.0    9     103
1285     7.000   3.9000    3.0000   75.00    1.0    9     103
1333    10.600   9.0000    3.3000  137.00   12.0    9     103
1483    16.000   9.0000    3.4000  158.60    8.0    9     103
1580    10.800   5.0000    2.8000   99.40    1.0    9     103
...        ...      ...       ...     ...    ...  ...     ...
996      0.500   0.1000   80.1000  323.00  180.0   18      44
1861     0.040   0.0300   90.3000  339.40  180.0   18      44
2028     0.056   0.0067    0.0112    0.34  180.0    3      31
1372     6.300  26.7000   61.5000  511.00    7.0   15      84
1440     6.200  27.0000   32.0000  400.00    1.0   15      84
1455     8.000  10.8000   48.8000  324.00    1.0   15      84
1456     8.000   7.7000   58.5000  355.00    1.0   15      84
1449     5.100  21.0000   39.0000  370.00    1.0   15      84
1448     5.700  26.0000   33.0000  390.00    1.0   15      84
1451     3.800  15.0000   46.0000  330.00    1.0   15      84
1323     3.500  13.0000   59.0000  370.00    2.0   15      84
1454     7.500   2.0000   50.0000  250.00    1.0   15      47
1597     6.000   1.0000   46.0000  220.00    1.0   15      47
1453     8.000   4.0000   56.0000  290.00    1.0   15     110
1444     8.000   0.8000   47.0000  230.00    1.0   15     110
1446     7.000   1.0000   50.0000  240.00    1.0   15     110
1919    10.700   3.4000   56.3000  298.60    1.0   15     110
1920     7.100   0.6000   59.3000  271.00    1.0   15     110
1921     7.800   0.6000   56.2000  261.40    1.0   15     110
1923     8.300   2.3000   56.1000  278.30    1.0   15     110
1452     8.800  20.0000   36.0000  360.00    1.0   15     101
1450    11.000  23.0000   38.0000  400.00    1.0   15     101
1457     3.200   7.8000   30.8000  206.20    1.0   15     101
1463    14.200  11.7000   29.3000  279.30    1.0   15     101
1462     5.200  15.9000   28.0000  275.90    1.0   15     101
1460    12.000  10.5000   30.3000  263.70    1.0   15     101
1441     8.000   0.7000   55.0000  260.00    1.0   15      13
1442     8.000   6.0000   44.0000  265.00    1.0   15      13
1439     7.000   0.7000   48.0000  230.00    1.0   15      13
1598    14.500   3.2000    7.4000  116.40   36.0   16      62

[989 rows x 7 columns]

### Обучаем???

**Yandex Time!!!**

In [0]:
new_dataset = []
 # То что он купил
id_tovs = list(map(int, row[0].split()))
all_tovs = set(meta.index)

meta_dict = meta.T.to_dict('list')


for (index,row) in train.iterrows():
    
    # То что он купил
    id_tovs = list(map(int, row[0].split()))
    
    # То что он не купил *hint1
    # sample - это рандомное разделение данн
    not_tov = list(set(id_tovs) ^ all_tovs) 
    
    # Тут я взял рандомные товаров, которые чувак не купил в том же количестве что и купил
    # По хорошему тут нужно провернуть тот хинт с рыбой, который я описал выше
    # hint3
    for id_tov in sample(not_tov, len(id_tovs)):
        # Для каждого товара купленного пользователем - достанем его фичи и проставим 1
        # Это будет означать что он купил эти товары *hint2
        new_dataset.append([index, *meta_dict[id_tov], 1])
    
    for id_tov in sample(not_tov, 5 * len(id_tovs)):
        # Для каждого товара купленного пользователем - достанем его фичи и проставим 0
        # Это будет означать что он не купил эти товары *hint2
        new_dataset.append([index, *meta_dict[id_tov], 0])


In [0]:
dataset = pd.DataFrame(new_dataset, columns=['buyer','belki', 'jiri', 'uglevodi', 'kkal',  'time', 'cat', 'subcat', 'answer'])

In [0]:
dataset

buyer  belki   jiri  uglevodi   kkal   time   cat  subcat  answer
0              4  11.00  10.30      21.6  223.0  720.0   2.0    89.0       1
1              4  13.00   5.20      10.5  141.0   18.0   6.0    60.0       1
2              4  21.40  36.80      32.3  541.7   90.0  18.0   106.0       1
3              4   2.90   9.60      11.6  144.0  720.0   2.0    97.0       1
4              4   7.50   1.60      73.1  341.0  270.0   2.0   114.0       1
5              4   2.00  13.00      15.0  185.0   18.0   6.0    61.0       1
6              4   7.50   2.00      50.0  250.0    1.0  15.0    47.0       0
7              4   7.40   0.80      50.0  242.0    4.0  19.0    54.0       0
8              4   5.10   1.00      43.0  202.0    5.0  19.0   111.0       0
9              4   2.00  65.00       6.0  617.0    7.0   2.0    91.0       0
10             4   1.50   0.30       9.0   45.0  730.0   7.0    56.0       0
11             4  11.00  10.30      21.6  223.0  720.0   2.0    89.0       0
12             4   3.80  20.80      40.4  364.0    3.0  18.0    70.0       0
13             4  15.20   3.80       6.0  119.0    4.0   8.0     9.0       0
14             4   1.30   0.70       4.7   30.3  365.0  12.0    88.0       0
15             4   6.80   8.50      56.0  330.0  360.0  18.0   106.0       0
16             4   2.90   2.50      10.5   76.1    6.0   4.0    16.0       0
17             4   9.00  20.00      14.0  272.0    5.0  11.0    59.0       0
18             4  12.80  16.50      10.5  242.0    4.0   9.0   103.0       0
19             4   6.00   2.50      12.2   95.3    7.0   9.0    29.0       0
20             4   8.00   6.00      45.0  275.0    4.0  19.0   109.0       0
21             4   9.80   1.20      52.8  261.2    3.0  19.0    54.0       0
22             4   0.45   1.05      11.3   56.0  720.0   4.0    75.0       0
23             4  12.00   5.00      23.0  190.0  180.0   6.0    66.0       0
24             4   4.50   2.50      35.0  185.0    5.0  19.0   111.0       0
25             4   3.30   2.50       5.3   57.0    5.0   9.0    29.0       0
26             4  15.00  11.00      32.0  287.0    8.0   9.0   103.0       0
27             4   8.00   4.00      56.0  290.0    1.0  15.0   110.0       0
28             4   2.00   4.30      25.3  147.9  120.0   5.0    50.0       0
29             4  22.00   0.50       5.0   75.0    7.0  14.0    25.0       0
...          ...    ...    ...       ...    ...    ...   ...     ...     ...
3492102  1442693   1.60   0.30      71.1  293.5  360.0   2.0    97.0       0
3492103  1442693  13.30  38.50       8.6  434.3    6.0  11.0    58.0       0
3492104  1442693  13.60   7.90      27.2  234.3  180.0   6.0    66.0       0
3492105  1442693   9.30  24.60      58.6  468.0    3.0  18.0    67.0       0
3492106  1442693  12.60  11.70      27.7  260.0    3.0  19.0   111.0       0
3492107  1442693  12.00  16.00       1.0  196.0    3.0  10.0    90.0       0
3492108  1442693   4.80   8.50      28.2  208.5    3.0   8.0    17.0       0
3492109  1442693   6.20  35.00      55.4  552.0  360.0  18.0   117.0       0
3492110  1442693  12.00   1.00      67.0  325.0   30.0   2.0    41.0       0
3492111  1442693  10.70   1.30      15.7  117.3    4.0   8.0     9.0       0
3492112  1442693  16.20  10.00       1.1  159.2  360.0   6.0    63.0       0
3492113  1442693   2.00  12.40       7.6  134.0   45.0   2.0    91.0       0
3492114  1442693  11.60  16.70      45.0  377.0    5.0  19.0   112.0       0
3492115  1442693  14.80  64.00      13.7  698.0  180.0   2.0    97.0       0
3492116  1442693   7.00   5.90       5.0  101.0    3.0   8.0    95.0       0
3492117  1442693   2.00  28.00      53.0  472.0  360.0  18.0   106.0       0
3492118  1442693   8.30  23.80      56.6  473.8    4.0  18.0    70.0       0
3492119  1442693   7.00  43.00      46.0  601.0  360.0  18.0   117.0       0
3492120  1442693   4.40  10.50      55.8  255.3    7.0  18.0    69.0       0
3492121  1442693   8.00   7.70      58.5  355.0    1.0  15.0    84.0       0
3492122

In [0]:
# dataset.to_csv('dataset.csv')
# dataset['buyer']
# dataset=pd.read_csv('dataset.csv')

In [0]:
scaler =  StandardScaler()
scaled = dataset.copy()
# scaled = scaled.drop(columns=[scaled.columns[0]])
to_scale = ['belki', 'jiri', 'uglevodi', 'kkal', 'time', 'cat', 'subcat',]
features = scaled[to_scale]
scaler = StandardScaler().fit(features.values)
features = scaler.transform(features.values)
scaled[to_scale] = features

### Models!

In [0]:
old_dataset = dataset.copy()
dataset = scaled

In [0]:
model = LogisticRegression(max_iter=20000)
# samp = scaled.sample(frac=0.05)
model.fit(dataset[dataset.columns.difference(['answer'])], dataset['answer'])

/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=20000, multi_class='warn',
          n_jobs=None, penalty='l2', random_state=None, solver='warn',
          tol=0.0001, verbose=0, warm_start=False)

In [0]:
dataset

buyer     belki      jiri  uglevodi      kkal      time       cat  \
0       -1.731343 -0.022526 -0.829417  1.384379  0.174129 -0.621454  1.495388   
1       -1.731343 -0.783908  0.581156  0.503671  0.664166 -0.621454  1.337817   
2       -1.731343 -0.910805 -0.162728 -0.883858 -0.813582 -0.616845 -0.395467   
3       -1.731343 -0.276320 -0.724150  0.665688 -0.214082 -0.621454  1.495388   
4       -1.731343  1.389204  2.918076 -0.568133  2.263467  1.023997 -1.340895   
5       -1.731343  2.261621  2.560169 -0.759230  1.994265 -0.497008 -1.340895   
6       -1.731343  0.437476  0.665369  0.420586  0.861453  0.470904 -1.340895   
7       -1.731343 -0.879081 -0.331155  0.104861 -0.340091 -0.630672  0.707532   
8       -1.731343 -0.434941 -0.738186 -0.343802 -0.901406 -0.621454  1.180246   
9       -1.731343  0.469200 -0.808364  1.899509  0.586523  1.023997 -1.340895   
10      -1.731343  1.040237 -0.527653  0.013466 -0.245903 -0.612236 -0.395467   
11      -1.731343  0.009199  0.342552 -0.152705  0.193221 -0.621454  1.337817   
12      -1.731343 -0.165285 -0.345190  1.874584  0.797812 -0.626063  1.337817   
13      -1.731343  0.167820 -0.190799  1.031265  0.511427 -0.621454 -0.395467   
14      -1.731343 -0.942529 -0.871524 -1.008486 -1.474176 -0.612236 -0.237896   
15      -1.731343  0.358165 -0.036408 -0.011459  0.027754 -0.552318 -0.710610   
16      -1.731343 -0.942529 -0.653973 -1.008486 -1.295981 -0.612236 -0.237896   
17      -1.731343  0.142440  0.047805  1.442539  0.946732 -0.220462 -1.340895   
18      -1.731343 -1.228048 -0.246942 -0.759230 -0.856857 -0.593800 -0.553039   
19      -1.731343 -0.641149 -0.057462  0.794471  0.344051  0.470904 -1.340895   
20      -1.731343  0.453338  0.293427  0.694768  0.746899 -0.612236  1.495388   
21      -1.731343  0.072647 -0.868717  1.305447  0.109215  2.683275 -1.340895   
22      -1.731343  1.547825 -0.457475 -0.966944 -0.710483  0.194358 -0.710610   
23      -1.731343  4.276112 -0.352208 -1.137269  0.333232  1.023997 -1.340895   
24      -1.731343 -0.736322 -0.141675  1.226516  0.524792 -0.626063  1.337817   
25      -1.731343  0.262993 -0.611866  0.075781 -0.403733 -0.612236 -1.498466   
26      -1.731343 -0.910805  0.110965 -0.053002 -0.081072 -0.082189 -0.868181   
27      -1.731343 -0.958391 -0.773275  1.924435  0.403237  0.194358 -1.340895   
28      -1.731343 -1.053564 -0.653973  0.042546 -0.669753 -0.612236  1.337817   
29      -1.731343 -0.625287 -0.710115  0.084089 -0.621385 -0.626063 -0.395467   
...           ...       ...       ...       ...       ...       ...       ...   
3492102  1.731665 -0.276320  0.068858  0.163021  0.065939 -0.621454 -0.395467   
3492103  1.731665  0.358165  2.209280  0.237798  2.038814  0.609177  1.337817   
3492104  1.731665  1.468515 -0.317119 -1.133115 -0.697755 -0.626063 -0.080325   
3492105  1.731665  0.278855 -0.345190 -0.534898 -0.525924 -0.552318 -0.710610   
3492106  1.731665 -0.879081 -0.632919 -0.991869 -1.258433 -0.612236 -0.237896   
3492107  1.731665 -0.831494  0.146054 -0.161013 -0.105892 -0.082189 -0.868181   
3492108  1.731665 -0.514252  0.033770  0.736311  0.403237 -0.566145  1.337817   
3492109  1.731665 -1.307358 -0.871524 -0.987715 -1.493269  2.729366 -1.025752   
3492110  1.731665 -0.434941 -0.808364  0.736311 -0.252267 -0.630672  0.707532   
3492111  1.731665  0.199544  0.875903 -0.759230  0.403237  0.609177 -1.340895   
3492112  1.731665  0.358165  1.998747  0.487054  1.975173 -0.082189  1.337817   
3492113  1.731665 -0.752184 -0.871524 -0.260716 -0.984140 -0.552318 -0.710610   
3492114  1.731665  1.547825  1.402236  0.370735 -1.639643  0.609177 -1.340895   
3492115  1.731665 -0.704597 -0.513617  1.965978  0.679439 -0.427872  1.337817   
3492116  1.731665  0.992651  0.525014 -1.091572 -0.061343 -0.626063 -0.080325   
3492117  1.731665 -0.942529 -0.597830 -1.000178 -1.245068 -0.630672 -0.237896   
3492118  1.731665 -0.276320 -0.464493 -0.194248 -0.535470 -0.621454 -0.395467   
3492119  1.731665 -1.005978 -0.857488 -0.85

In [0]:
from sklearn.ensemble import RandomForestRegressor as RFR
rfr = RFR(verbose=10, n_estimators=3)
rfr.fit(dataset[dataset.columns.difference(['answer'])], dataset['answer'])

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


building tree 1 of 3


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   38.8s remaining:    0.0s


building tree 2 of 3


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:  1.4min remaining:    0.0s


building tree 3 of 3


[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:  2.0min remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:  2.0min finished


RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=3, n_jobs=None,
           oob_score=False, random_state=None, verbose=10,
           warm_start=False)

In [0]:
model=rfr

## Predictions!

In [0]:
scaler =  StandardScaler()
scaled_meta = meta.copy()
to_scale = ['belki', 'jiri', 'uglevodi', 'kkal', 'cat', 'subcat','time']
features = scaled_meta[to_scale]
scaler = StandardScaler().fit(features.values)
features = scaler.transform(features.values)
scaled_meta[to_scale] = features
scaled_meta

belki      jiri  uglevodi      kkal      time       cat    subcat
id_tov                                                                      
81     -0.910148 -0.652432 -0.977967 -1.268151 -0.610775 -0.237903 -0.377909
109    -0.910148 -0.596249 -0.977967 -1.223596 -0.606162 -0.237903 -0.377909
1785   -0.910148 -0.701593 -0.977967 -1.312705 -0.610775 -0.237903 -0.377909
377    -0.910148 -0.652432 -0.977967 -1.268151 -0.610775 -0.237903 -0.377909
596    -0.910148 -0.806936 -0.977967 -1.395449 -0.610775 -0.237903 -0.377909
395     0.646327  0.281611 -0.737120 -0.109732 -0.615389 -0.237903  1.145583
307    -0.274852 -0.406631 -0.757883 -0.833425 -0.606162 -0.237903  1.145583
512    -0.274852 -0.455792 -0.799408 -0.898984 -0.606162 -0.237903  1.145583
818    -0.227205 -0.455792 -0.737120 -0.854430 -0.606162 -0.237903  1.145583
826    -0.274852 -0.455792 -0.757883 -0.873525 -0.606162 -0.237903  1.145583
927     0.328679 -0.526020 -1.056865 -1.017372 -0.629228 -0.237903  1.145583
1695    0.995740 -0.104647  0.238724  0.227609 -0.601549 -0.237903  1.145583
1696    0.995740 -0.104647  0.155673  0.291259 -0.601549 -0.237903  1.145583
1832    0.836916  0.386955 -1.056865 -0.173382 -0.610775 -0.237903  1.145583
1849    1.472212 -0.806936 -1.090086 -1.086750 -0.610775 -0.237903  1.145583
2038   -0.274852 -0.455792 -0.654070 -0.809875 -0.606162 -0.237903  1.145583
33      0.995740 -0.596249 -1.110848 -1.000823 -0.610775 -0.237903  1.145583
87      1.154564 -0.526020 -1.048560 -0.879890 -0.620002 -0.237903  1.145583
90      1.154564 -0.245105 -1.048560 -0.650752 -0.620002 -0.237903  1.145583
467     0.995740 -0.104647  0.155673  0.176690 -0.596936 -0.237903  1.145583
472    -0.274852 -0.455792 -0.674833 -0.835335 -0.606162 -0.237903  1.145583
503    -0.116028 -0.561135 -1.069323 -1.121757 -0.606162 -0.237903  1.145583
526     0.836916 -0.104647  0.197199  0.176690 -0.601549 -0.237903  1.145583
1097   -0.227205 -0.455792 -0.757883 -0.865887 -0.606162 -0.237903  1.145583
1151    1.154564 -0.526020 -1.048560 -0.879890 -0.596936 -0.237903  1.145583
1231   -0.290735 -0.455792 -1.007035 -1.007188 -0.610775 -0.237903  1.145583
1278    0.296914  0.007719 -0.110088 -0.007893 -0.601549 -0.237903  1.145583
1285   -0.274852 -0.603272 -1.048560 -1.172677 -0.629228 -0.237903  1.145583
1333    0.296914 -0.245105 -1.036103 -0.778051 -0.578483 -0.237903  1.145583
1483    1.154564 -0.245105 -1.031950 -0.640568 -0.596936 -0.237903  1.145583
...          ...       ...       ...       ...       ...       ...       ...
1323   -0.830736  0.035810  1.276856  0.704980 -0.624615  0.708422  0.601479
1454   -0.195440 -0.736707  0.903129 -0.058813 -0.629228  0.708422 -0.405115
1597   -0.433676 -0.806936  0.737028 -0.249761 -0.629228  0.708422 -0.405115
1453   -0.116028 -0.596249  1.152281  0.195785 -0.629228  0.708422  1.336019
1444   -0.116028 -0.820982  0.778553 -0.186111 -0.629228  0.708422  1.336019
1446   -0.274852 -0.806936  0.903129 -0.122462 -0.629228  0.708422  1.336019
1919    0.312797 -0.638387  1.164738  0.250523 -0.629228  0.708422  1.336019
1920   -0.258970 -0.835027  1.289314  0.074851 -0.629228  0.708422  1.336019
1921   -0.147793 -0.835027  1.160586  0.013748 -0.629228  0.708422  1.336019
1923   -0.068381 -0.715638  1.156433  0.121315 -0.629228  0.708422  1.336019
86     -0.386029  0.070925 -0.118394 -0.069633 -0.629228  0.708422  1.091172
88     -0.433676  0.429092 -0.093478  0.230155 -0.629228  0.708422  1.091172
94     -0.338382  0.021765 -0.180681 -0.140284 -0.629228  0.708422  1.091172
89     -0.322499  0.084971  0.010335  0.025204 -0.629228  0.708422  1.091172
93     -0.354264  0.162222 -0.010428  0.076124 -0.629228  0.708422  1.091172
91     -0.433676  0.155199 -0.010428  0.057666 -0.629228  0.708422  1.091172
1452    0.011031  0.527412  0.321775  0.641330 -0.629228  0.708422  1.091172
1450    0.360444  0.738099  0.404825  0.895928 -0.629228  0.708422  1.091172
1457   -0.878383 -0.329380  0.105843 -0.337597 -0.629228  0.708422  1.091172
1463   

In [0]:
new_meta_dict = meta.T.to_dict('list')
items = new_meta_dict.items()
values = [i[1] for i in items]
keys = [i[0] for i in items]
# to_train = np.array([([13, *val]) for val in values])

# to_train = pd.DataFrame(to_train)
# to_train=to_train.rename(columns={1: 'buyer', 0:'belki', 2:'jiri', 5:'uglevodi', 3:'kkal', 4:'time',})

In [0]:
person=159
to_train = np.array([[person, *val] for val in values])
#     train_data = FeaturesData(num_feature_data=np.array(to_train[:, :-2], dtype=np.float32), 
#                              cat_feature_data=np.array(to_train[:, -2:], dtype=np.object),
#                              num_feature_names=['buyer', 'belki', 'jiri', 'uglevodi', 'kkal', 'time'],
#                              cat_feature_names=['cat', 'subcat']
#                              )
#person_answer = list(sorted([[pr, it] for it, pr in zip(keys, predicted)]))[100:]
# train_pool = Pool(dataset[dataset.columns.difference(['answer'])], cat_features=['cat', 'subcat'])

predicted = model.predict(to_train)
person_answer = list(sorted([[pr, it] for it, pr in zip(keys, predicted)]))[::-1][:100]
person_answer

[[0, 2063],
 [0, 2062],
 [0, 2061],
 [0, 2059],
 [0, 2058],
 [0, 2057],
 [0, 2056],
 [0, 2055],
 [0, 2054],
 [0, 2053],
 [0, 2052],
 [0, 2051],
 [0, 2041],
 [0, 2040],
 [0, 2039],
 [0, 2038],
 [0, 2036],
 [0, 2034],
 [0, 2033],
 [0, 2032],
 [0, 2031],
 [0, 2030],
 [0, 2029],
 [0, 2028],
 [0, 2026],
 [0, 2022],
 [0, 2021],
 [0, 2016],
 [0, 2013],
 [0, 2009],
 [0, 2008],
 [0, 2007],
 [0, 2001],
 [0, 2000],
 [0, 1996],
 [0, 1995],
 [0, 1984],
 [0, 1983],
 [0, 1981],
 [0, 1979],
 [0, 1978],
 [0, 1976],
 [0, 1975],
 [0, 1974],
 [0, 1966],
 [0, 1965],
 [0, 1963],
 [0, 1961],
 [0, 1960],
 [0, 1959],
 [0, 1956],
 [0, 1953],
 [0, 1949],
 [0, 1948],
 [0, 1944],
 [0, 1941],
 [0, 1938],
 [0, 1936],
 [0, 1935],
 [0, 1934],
 [0, 1933],
 [0, 1932],
 [0, 1931],
 [0, 1930],
 [0, 1929],
 [0, 1927],
 [0, 1924],
 [0, 1923],
 [0, 1922],
 [0, 1921],
 [0, 1920],
 [0, 1919],
 [0, 1917],
 [0, 1913],
 [0, 1911],
 [0, 1910],
 [0, 1908],
 [0, 1905],
 [0, 1904],
 [0, 1903],
 [0, 1900],
 [0, 1898],
 [0, 1895],
 [0,

In [0]:
submission = []

#
# Если у вас много оперативной памяти - то лучше засуньте
# Все фичи в 1 список и сделайте predict 1 раз
# Это значительно ускорит процесс
# Ещё можно узнать какие продукты точно не покупают и вообще не добавлять их
#

# Для каждого человека
for person in tqdm(train.index):
    to_train = np.array([([person, *val]) for val in values])
#     train_data = FeaturesData(num_feature_data=np.array(to_train[:, :-2], dtype=np.float32), 
#                              cat_feature_data=np.array(to_train[:, -2:], dtype=np.object),
#                              num_feature_names=['buyer', 'belki', 'jiri', 'uglevodi', 'kkal', 'time'],
#                              cat_feature_names=['cat', 'subcat']
#                              )
    #person_answer = list(sorted([[pr, it] for it, pr in zip(keys, predicted)]))[100:]
    # train_pool = Pool(dataset[dataset.columns.difference(['answer'])], cat_features=['cat', 'subcat'])
    predicted = model.predict(to_train)
    person_answer = list(sorted([[pr, it] for it, pr in zip(keys, predicted)]))[100:]
    predicted = model.predict(to_train)
    submission.append(' '.join([str(i[1]) for i in person_answer]))

100%|██████████| 65950/65950 [03:12<00:00, 343.21it/s]


In [0]:
submission

['315 316 318 319 321 322 323 329 331 332 335 336 337 338 339 341 344 345 349 351 352 356 359 360 362 363 370 371 372 373 374 376 377 378 379 380 381 382 383 385 386 388 389 391 392 393 394 395 396 398 403 408 409 415 417 419 420 422 424 425 426 428 433 434 438 443 444 445 450 453 456 457 458 460 462 465 466 467 470 471 472 477 478 479 480 482 483 484 485 487 488 489 490 491 492 493 494 495 497 500 501 503 506 510 511 512 514 516 517 518 520 522 523 524 525 526 527 528 529 532 534 535 537 538 539 540 541 545 548 549 552 559 560 561 562 563 564 565 567 568 569 570 571 574 575 577 578 580 583 584 586 589 593 596 598 599 602 611 612 613 614 625 626 627 629 630 634 635 637 640 642 643 646 647 653 659 662 663 665 667 668 669 670 671 672 673 674 675 676 677 678 679 681 682 683 685 686 687 688 689 690 691 692 698 699 701 702 709 710 714 715 716 718 719 721 726 727 728 731 735 736 738 739 740 741 743 744 745 746 747 748 749 750 752 753 754 756 757 759 762 763 764 766 767 768 769 772 773 774 77

In [0]:
answer = pd.DataFrame(index = train.index)
answer.index.names = ['buyer']
answer['items'] = submission

In [0]:
winsub = pd.read_csv('win_submission.csv')

In [0]:
for index, row in winsub.iterrows():
    row['items'] = "a"

In [0]:
answer

items
buyer                                                                                                 
4        2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
11       2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
34       2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
37       2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
44       2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
95       2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
119      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
121      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
134      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
159      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
166      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
198      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
205      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
211      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
219      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
240      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
253      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
271      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
304      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
322      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
336      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
363      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
364      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
374      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
383      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
387      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
392      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
394      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
454      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
495      2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
...                                                                                                ...
1441992  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
1442001  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
1442060  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
1442097  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
1442105  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
1442136  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335
1442144  2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 17

In [0]:
ultimate = "2028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 1335"

In [0]:
answer['items'][0]

'101 1874 1135 836 429 1640 1533 1775 1629 1914 1360 81 1458 87 291 71 23 90 248 247 377 505 437 733 58 2036 563 250 1646 64 249 293 668 65 273 671 222 1126 501 790 1375 290 1819 22 1095 220 139 2038 129 1149 1761 1785 245 246 292 294 1723 1586 1795 1904 1011 497 160 29 1420 968 1266 265 1579 363 269 1945 1959 20 1947 403 512 962 31 532 1197 1151 929 949 1288 580 1989 395 695 471 1099 644 824 335 503 680 1946 467 801 1346 1694 308 1671 356 28 841 1613 322 914 775 1204 1709 253 625 1548 931 1596 1083 185 1355 526 1082 472 1234 27 1696 1206 244 645 1705 371 688 274 33 829 1587 702 351 1654 194 1695 577 667 826 109 13 1062 1849 137 223 183 412 396 646 138 1948 673 1475 1832 4082028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 13352028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 13352028 1423 2062 1597 574 497 230 1685 626 1338 738 303 1666 1457 1878 1720 1551 1531 1529 13352028 1423 2062 1597 574 497 230 1685 6

In [0]:
# answer=winsub.copy()
name = 'submission-%s.csv' % datetime.now()
answer.to_csv(name, index=False)

In [0]:
answer

buyer  \
0            4   
1           11   
2           34   
3           37   
4           44   
5           95   
6          119   
7          121   
8          134   
9          159   
10         166   
11         198   
12         205   
13         211   
14         219   
15         240   
16         253   
17         271   
18         304   
19         322   
20         336   
21         363   
22         364   
23         374   
24         383   
25         387   
26         392   
27         394   
28         454   
29         495   
...        ...   
65920  1441992   
65921  1442001   
65922  1442060   
65923  1442097   
65924  1442105   
65925  1442136   
65926  1442144   
65927  1442239   
65928  1442295   
65929  1442297   
65930  1442307   
65931  1442383   
65932  1442422   
65933  1442455   
65934  1442526   
65935  1442529   
65936  1442551   
65937  1442570   
65938  1442576   
65939  1442590   
65940  1442603   
65941  1442633   
65942  1442643   
65943  1442651   
65944  1442667   
65945  1442668   
65946  1442673   
65947  1442677   
65948  1442691   
65949  1442693   

                                                                                                     items  
0      101 1874 1135 836 429 1640 1533 1775 1629 1914 1360 81 1458 87 291 71 23 90 248 247 377 505 437 ...  
1      1795 194 1475 1527 2067 1391 2017 447 1719 534 1214 81 1458 87 291 71 23 90 248 247 377 505 437 ...  
2      1458 2036 220 269 962 31 801 1671 1596 185 81 87 291 71 23 90 248 247 377 505 437 733 58 563 250...  
3      87 1819 1151 680 1234 1706 1708 1178 453 1214 1665 81 1458 291 71 23 90 248 247 377 505 437 733 ...  
4      437 249 1149 824 1234 975 261 657 986 1743 81 1458 87 291 71 23 90 248 247 377 505 733 58 2036 5...  
5      1646 1149 532 1946 1705 688 1706 975 80 800 81 1458 87 291 71 23 90 248 247 377 505 437 733 58 2...  
6      65 968 580 28 1083 274 1470 136 1111 14 1546 81 1458 87 291 71 23 90 248 247 377 505 437 733 58 ...  
7      248 247 377 505 31 931 1234 360 843 374 81 1458 87 291 71 23 90 437 733 58 2036 563 250 1646 64 ...  
8      81 71 505 220 139 1723 1596 351 1182 136 1458 87 291 23 90 248 247 377 437 733 58 2036 563 250 1...  
9      291 290 1288 1346 1948 508 118 540 762 1740 81 1458 87 71 23 90 248 247 377 505 437 733 58 2036 ...  
10     869 1547 682 683 1903 1073 1354 1235 933 1247 932 81 1458 87 291 71 23 90 248 247 377 505 437 73...  
11     733 265 1947 1204 645 646 817 948 81 1458 87 291 71 23 90 248 247 377 505 437 58 2036 563 250 16...  
12     1458 87 505 437 668 294 1099 503 1613 673 81 291 71 23 90 248 247 377 733 58 2036 563 250 1646 6...  
13     222 1126 220 1959 914 750 251 1779 1915 1270 81 1458 87 291 71 23 90 248 247 377 505 437 733 58 ...  
14     90 139 292 532 308 841 931 351 1990 81 1458 87 291 71 23 248 247 377 505 437 733 58 2036 563 250...  
15     23 377 437 58 1671 1475 362 1915 316 1342 327 1230 1521 81 1458 87 291 71 90 248 247 505 733 203...  
16     1646 2038 1795 1904 363 1959 898 2051 81 1458 87 291 71 23 90 248 247 377 505 437 733 58 2036 56...  
17     377 249 1959 929 308 137 818 81 1458 87 291 71 23 90 248 247 505 437 733 58 2036 563 250 1646 64...  
18     1646 1795 356 274 592 1306 313 81 1458 87 291 71 23 90 248 247 377 505 437 733 58 2036 563 250 6...  
19     1458 90 377 563 1266 403 335 81 87 291 71 23 248 247 505 437 733 58 2036 250 1646 64 249 293 668...  
20     403 1178 453 1612 1719 1390 1611 894 211 1225 813 81 1458 87 291 71 23 90 248 247 377 505 437 73...  
21     81 1458 292 1723 497 160 1959 1346 625 138 674 87 291 71 23 90 248 247 377 505 437 733 58 2036 5...  
22     1458 363 185 351 109 1475 1973 2017 81 87 291 71 23 90 248 247 377 505 437 733 58 2036 563 250 1...  
23     1458 733 501 129 509 1751 1256 81 87 291 71 23 90 248 247 377 505 437 58 2036 563 250 1646 64 24...  
24     248 247 505 437 471 297 1756 1958 118 81 1458 87 291 71 23 90 377 733 58 2036 563 250 1646 64 24...  
25     81 23 58 269 137 50 1877 1115 212 1458 87 291 71 90

In [0]:
# Внимание - выходной файл будет размером в 700мб
# Это можно загрузить в кагл, но лучше загрузить zip файл
# Он будет весить 5мб

name = 'submission-%s.csv' % datetime.now()
answer = pd.DataFrame(index = train.index)
answer.index.names = ['buyer']
answer['items'] = submission
answer.to_csv(name)



ValueError: Wrong number of items passed 2, placement implies 1

In [0]:
zip_obj = ZipFile("%s.zip" % name, 'w', ZIP_DEFLATED)
zip_obj.write(name, os.path.basename(name))
zip_obj.close()